In [1]:
# import packages
#import matplotlib
#matplotlib.use("nbagg")

import numpy as np
from plotly.offline import init_notebook_mode

import matplotlib.pyplot as plt
from mpl_toolkits.mplot3d import Axes3D

import functools
from itertools import product as all_combinations

# import local
import Mesh
import utils
# to store files
import pickle

# run plotly offline
init_notebook_mode(connected=True)
visualize = True

# Load mesh

In [2]:
mesh_name = 'sphere'
mesh = Mesh.Mesh("../models/" + mesh_name + ".off")
if visualize:
    mesh.visualize(plot_edges= True, quad_mesh = False)

Loading "../models/sphere.off" ..
Computing face and vertex normals ..
Building adjacency list ..
Building vert2edge map..
Mesh generated: vertices = 258, faces = 512 


# Apply axis alligning deformation

In [3]:
mesh.align_normals(iterations = 5)
if visualize:
    mesh.visualize(plot_edges=True)
#store in pkl file
with open('mesh.pkl', 'wb') as output:
    pickle.dump(mesh, output, pickle.HIGHEST_PROTOCOL)

Aligning normals (1/5) ..
Solved linear systems..
refreshed normals
Aligning normals (2/5) ..
Solved linear systems..
refreshed normals
Aligning normals (3/5) ..
Solved linear systems..
refreshed normals
Aligning normals (4/5) ..
Solved linear systems..
refreshed normals
Aligning normals (5/5) ..
Solved linear systems..
refreshed normals


In [4]:
cube = Mesh.Mesh(shape_factory = 'cube', shape_resolution = 16)
# save cube mesh to file
with open('cube.pkl', 'wb') as output:
    pickle.dump(cube, output, pickle.HIGHEST_PROTOCOL)
if visualize:
    cube.visualize(plot_edges=True, quad_mesh = True)

generating cube..
Computing face and vertex normals ..
Building adjacency list ..
Building vert2edge map..
Mesh generated: vertices = 1538, faces = 3072 


In [5]:
# downscale and center mesh
with open('mesh.pkl', 'rb') as input:
    mesh = pickle.load(input)
with open('cube.pkl', 'rb') as input:
    cube = pickle.load(input)

bounding_box = mesh.compute_bounding_box()
scaling_factor = 1.0/ max(max(bounding_box[1]-bounding_box[0],bounding_box[3]-bounding_box[2]),bounding_box[5]-bounding_box[4])
# scale mesh
mesh.scale(scaling_factor)
bounding_box = mesh.compute_bounding_box()

S = np.eye(3)
S[0,0]= (bounding_box[1]-bounding_box[0])
S[1,1]= (bounding_box[3]-bounding_box[2])
S[2,2]= (bounding_box[5]-bounding_box[4])
t = np.asarray([0.0,0.0,0.0])
cube.apply_scalingtranslation(S,t)

bbc = cube.compute_bounding_box()
center_bbc = (0.5 * np.asarray([bbc[1]+bbc[0],bbc[3]+bbc[2],bbc[5]+bbc[4]]))
center = 0.5 * np.asarray([bounding_box[1]+bounding_box[0],bounding_box[3]+bounding_box[2],bounding_box[5]+bounding_box[4]])
R = np.eye(3)
t = center-center_bbc
cube.apply_rototranslation(R,t)

utils.display_meshes([cube,mesh])


refreshed normals
refreshed normals
refreshed normals


# Get map to orginal mesh

In [6]:
# TODO: optimize!!
closest_points, simplex_indices, barycentric_cordinates, min_distances = mesh.closest_point_projection(cube.vertices)

Working on point  0
Working on point  1
Working on point  2
Working on point  3
Working on point  4
Working on point  5
Working on point  6
Working on point  7
Working on point  8
Working on point  9
Working on point  10
Working on point  11
Working on point  12
Working on point  13
Working on point  14
Working on point  15
Working on point  16
Working on point  17
Working on point  18
Working on point  19
Working on point  20
Working on point  21
Working on point  22
Working on point  23
Working on point  24
Working on point  25
Working on point  26
Working on point  27
Working on point  28
Working on point  29
Working on point  30
Working on point  31
Working on point  32
Working on point  33
Working on point  34
Working on point  35
Working on point  36
Working on point  37
Working on point  38
Working on point  39
Working on point  40
Working on point  41
Working on point  42
Working on point  43
Working on point  44
Working on point  45
Working on point  46
Working on point  47
Wo

In [7]:
mapped_cube = cube
mesh = Mesh.Mesh("../models/" + mesh_name + ".off")
# loop over cube vertices
for i in range(cube.nverts):
    v0 = mesh.vertices[mesh.faces[simplex_indices[i].astype(int),2]] - mesh.vertices[mesh.faces[simplex_indices[i].astype(int),0]]
    v1 = mesh.vertices[mesh.faces[simplex_indices[i].astype(int),1]] - mesh.vertices[mesh.faces[simplex_indices[i].astype(int),0]]
    # map to new position   
    mapped_cube.vertices[i,:] = mesh.vertices[mesh.faces[simplex_indices[i].astype(int),0]]+ barycentric_cordinates[i,0]*v0 +barycentric_cordinates[i,1]*v1
    
mapped_cube.refresh_normals()

mapped_cube.visualize(plot_edges= True)

# export for tensorflow
cube.export_for_tensorflow(outfile = mesh_name + '.npy')

with open('cube_mapped.pkl', 'wb') as output:
    pickle.dump(mapped_cube, output, pickle.HIGHEST_PROTOCOL)


Loading "../models/sphere.off" ..
Computing face and vertex normals ..
Building adjacency list ..
Building vert2edge map..
Mesh generated: vertices = 258, faces = 512 
refreshed normals
